# Additional Constraints

## release_time, deadline

各Taskには開始可能時刻(Release Time)と終了締め切り時刻(Deadline)を与えることができます。

![](image/release_time.drawio.svg)![](image/deadline.drawio.svg)

下記例では`Job A`の0番目のプロセスの開始時間は10以上、終了時間は20以下であることを指定します。

In [1]:
from amplify_sched import *

token = "xxxxxxxxxxxxxxxxxxxxxxxxx"

model = Model()
model.jobs.add("Job A")
model.machines.add("Machine X")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine X"] = 10
model.jobs["Job A"][0].release_time = 10
model.jobs["Job A"][0].deadline = 20
gantt = model.solve(token=token, timeout=1)
gantt.timeline()

## transportation_time

ある Machine からある Machine への輸送時間(transportation_time)を Task ごとに設定できます。輸送時間が設定されている場合、その時間より短い間隔では次の Task を開始できません。

![](image/transportation_time.drawio.svg)


下記例では`Machine A` から`Machine B`に`Job A`の0番目のプロセスの輸送時間を10に設定しています。

In [2]:
model = Model()
model.jobs.add("Job A")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 7
model.jobs["Job A"].append(Task())
model.jobs["Job A"][1].processing_times["Machine B"] = 5
model.jobs["Job A"][0].transportation_times.append((10, "Machine A", "Machine B"))
gantt = model.solve(token=token, timeout=1)
gantt.timeline()

## setup_time

ある Machine において、ある Task からある Task への切り替えにかかる準備時間(setup_time)を設定できます。準備時間が設定されている場合、その時間より短い間隔では次の Task を開始できません

![](image/setup_time.drawio.svg)

下記例では`Machine A` において、`Task[Job A, 0]`<->`Task[Job B,1]`の切り替えにかかる準備時間を10に設定しています。

In [3]:
model = Model()
model.jobs.add("Job A")
model.jobs.add("Job B")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 7
model.jobs["Job B"].append(Task())
model.jobs["Job B"][0].processing_times["Machine B"] = 7
model.jobs["Job B"].append(Task())
model.jobs["Job B"][1].processing_times["Machine A"] = 5
model.machines["Machine A"].setup_times.append((10, model.jobs["Job A", 0], model.jobs["Job B", 1]))
model.machines["Machine A"].setup_times.append((10, model.jobs["Job B", 1], model.jobs["Job A", 0]))
gantt = model.solve(token=token, timeout=1)
gantt.timeline(machine_view=True)

## maintenance_time

ある Machine が稼働できない時間区間を設定できます。設定した時間区間ではその Machine では Task を行うことはできません。

![](image/maintenance_time.drawio.svg)


下記例では`Machine A`は10~15をmaintenance_timeにしています。

In [4]:
model = Model()
model.jobs.add("Job A")
model.jobs.add("Job B")
model.jobs.add("Job C")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 7
model.jobs["Job B"].append(Task())
model.jobs["Job B"][0].processing_times["Machine B"] = 7
model.jobs["Job B"].append(Task())
model.jobs["Job B"][1].processing_times["Machine A"] = 5
model.jobs["Job C"].append(Task())
model.jobs["Job C"][0].processing_times["Machine A"] = 10
model.machines["Machine A"].maintenance_times.append(TimeRange(10, 15))
gantt = model.solve(token=token, timeout=1)
gantt.timeline(machine_view=True)

## buffer

ある Machine で終了した Task を、次の Machine での処理が始まるまで保管する倉庫を考えます。このとき、各 Machine の倉庫の容量と各 Task が占有するサイズを設定することができます。これらが設定されている場合、各時刻において倉庫の容量を超えるようなスケジュールは許されません。

![](image/buffer.drawio.svg)


下記例では`Machine A`のバッファを1に、`Task["Job A",0]`,`Task["Job B",0]`,`Task["Job C",1]`の要求バッファサイズを1に設定しています。

In [46]:
model = Model()
model.jobs.add("Job A")
model.jobs.add("Job B")
model.jobs.add("Job C")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 1
model.jobs["Job A"].append(Task())
model.jobs["Job A"][1].processing_times["Machine B"] = 3
model.jobs["Job B"].append(Task())
model.jobs["Job B"][0].processing_times["Machine A"] = 1
model.jobs["Job B"].append(Task())
model.jobs["Job B"][1].processing_times["Machine B"] = 2
model.jobs["Job C"].append(Task())
model.jobs["Job C"][0].processing_times["Machine A"] = 1
model.jobs["Job C"].append(Task())
model.jobs["Job C"][1].processing_times["Machine B"] = 7
model.jobs["Job A"][1].deadline = 4
model.jobs["Job B"][1].deadline = 6
model.machines["Machine A"].buffer_size = 1
model.machines["Machine A"].maintenance_times.append(TimeRange(3, 6))
model.jobs["Job A"][0].required_buffer_size = 1
model.jobs["Job B"][0].required_buffer_size = 1
model.jobs["Job C"][0].required_buffer_size = 1
gantt = model.solve(token=token, timeout=1)
gantt.timeline(machine_view=True)

## resource

各 Task を行うために必要なリソースを定義できます。各リソースには同時使用上限数が定められ、その数を超える複数の Task で同時にリソースを使用できません。

![](image/resource.drawio.svg)


下記例は`Task[Job A,0]`,`Task[Job B,0]`が`Resource A`を使用します。

In [51]:
model = Model()
model.jobs.add("Job A")
model.jobs.add("Job B")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.resources.add("Resource A")
model.resources["Resource A"].capacity = 1
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 10
model.jobs["Job A"][0].required_resources.append("Resource A")
model.jobs["Job B"].append(Task())
model.jobs["Job B"][0].processing_times["Machine B"] = 10
model.jobs["Job B"][0].required_resources.append("Resource A")

gantt = model.solve(token=token, timeout=1)
gantt.timeline(machine_view=True)

## no_wait

各 Job に no-wait フラグを設定できます。no-wait が設定された Job は一度 Task を始めたら、全 Task が終了するまで連続で Task を行う必要があります。

![](image/no_wait.drawio.svg)

下記例は`Job B`に`no_wait=True`を設定しています。

In [60]:
model = Model()
model.jobs.add("Job A")
model.jobs.add("Job B")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.machines.add("Machine C")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 10
model.jobs["Job A"].append(Task())
model.jobs["Job A"][1].processing_times["Machine B"] = 10
model.jobs["Job A"].append(Task())
model.jobs["Job A"][2].processing_times["Machine C"] = 10
model.jobs["Job B"].append(Task())
model.jobs["Job B"][0].processing_times["Machine B"] = 10
model.jobs["Job B"].append(Task())
model.jobs["Job B"][1].processing_times["Machine A"] = 15
model.jobs["Job B"].append(Task())
model.jobs["Job B"][2].processing_times["Machine C"] = 10
model.jobs["Job B"].no_wait = True
gantt = model.solve(token=token, timeout=1)
gantt.timeline()

## dependent_jobs

各 Job ごとに依存する Job を複数定義できます。依存する Job が定義されている場合、それらがすべて完了しないとその Job は開始できません。

![](image/dependent_jobs.drawio.svg)


下記例は`Job B`は`Job A`に依存すると設定しています。

In [62]:
model = Model()
model.jobs.add("Job A")
model.jobs.add("Job B")
model.machines.add("Machine A")
model.machines.add("Machine B")
model.machines.add("Machine C")
model.jobs["Job A"].append(Task())
model.jobs["Job A"][0].processing_times["Machine A"] = 10
model.jobs["Job A"].append(Task())
model.jobs["Job A"][1].processing_times["Machine B"] = 10
model.jobs["Job A"].append(Task())
model.jobs["Job A"][2].processing_times["Machine C"] = 10
model.jobs["Job B"].append(Task())
model.jobs["Job B"][0].processing_times["Machine B"] = 10
model.jobs["Job B"].append(Task())
model.jobs["Job B"][1].processing_times["Machine A"] = 15
model.jobs["Job B"].append(Task())
model.jobs["Job B"][2].processing_times["Machine C"] = 10
model.jobs["Job B"].dependent_jobs.append("Job A")
gantt = model.solve(token=token, timeout=1)
gantt.timeline()

## 複数の制約がある場合

### transportation_time + setup_time
transportation_time と setup_time が両方設定されている場合、それぞれ独立に制約を課します。すなわちある Machine における切り替え準備は前後の Task の輸送時間中にも行うことができます。

![](image/transportation_time+setup_time.drawio.svg)


### transportation_time + no_wait
no-wait フラグと transportation_time が両方設定されている場合、no-wait フラグが設定されている Job の連続する 2 つの Task(j, p), Task(j,p+1)について、Task(j,p+1) の処理開始時刻 = Task(j,p) の処理終了時刻 + transportation_time[Task(j,p), Machine A, Machine B] となります。

![](image/transportation_time+no_wait.drawio.svg)


### transportation_time + dependent_jobs
dependent_jobs によって Job A -> Job C という順序関係が定義されている場合、Job A の最後の工程に対して transportation_time を設定することができ、Job C の最初の工程は Job A の最後の工程から transportaion_time 以上経過しないと開始できません。

![](image/transportation_time+dependent_jobs.drawio.svg)


### transportation_time + buffer
buffer と transportation_time が両方設定されている場合、Task は輸送時間中には倉庫を使用しないとし、輸送直後に次のタスクが開始されると考えます。

![](image/transportation_time+buffer.drawio.svg)

